In [1]:
import pandas as pd
import hvplot.pandas
from pathlib import Path
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
import hvplot.pandas

import matplotlib.pyplot as plt
import numpy as np
import scipy.spatial

In [2]:
#setting path/reading
path = Path() / "Data" / "tenyear.csv"
tracks_df = pd.read_csv(path ,index_col=[0])
tracks_df.head(3)

acousticness                   artists  danceability  duration_ms   
7054      0.022200           ['Tame Impala']         0.450       362880  \
7055      0.000103  ['Bring Me The Horizon']         0.382       274133   
7056      0.852000             ['Daft Punk']         0.179       162120   

      energy  explicit                      id  instrumentalness  key   
7054   0.849         0  4m3GHOgCNZMv0we7H9j8Y8           0.00455    5  \
7055   0.943         0  0ZxZsjMMyLgjRV1XLWlIaS           0.00011    8   
7056   0.167         0  0Jc2SfIHv63JNsUZpunh54           0.74800    1   

      liveness  loudness  mode           name  popularity release_date   
7054    0.0792    -5.075     1    Expectation          48   2010-05-21  \
7055    0.3960    -5.434     1  It Never Ends          50   2010-10-05   
7056    0.1060   -23.408     1   Solar Sailer          48   2010-01-01   

      speechiness    tempo  valence  year  
7054       0.0570  139.925   0.1610  2010  
7055       0.0872  105.032   0.1280  2010  
7056       0.0394  124.266   0.0399  2010

In [3]:
#new df so we don't lose the original, might need song names and ids in the same place for later
cleaned_tracks_df = tracks_df.drop(['artists','explicit', 'mode','release_date','name','year','key', 'popularity'], axis=1, inplace=False)
cleaned_tracks_df = cleaned_tracks_df.set_index(['id'])
cleaned_tracks_df.to_csv("Data/tenyear_cleaned_for_kmeans.csv")
cleaned_tracks_df.head(3)

acousticness  danceability  duration_ms  energy   
id                                                                        
4m3GHOgCNZMv0we7H9j8Y8      0.022200         0.450       362880   0.849  \
0ZxZsjMMyLgjRV1XLWlIaS      0.000103         0.382       274133   0.943   
0Jc2SfIHv63JNsUZpunh54      0.852000         0.179       162120   0.167   

                        instrumentalness  liveness  loudness  speechiness   
id                                                                          
4m3GHOgCNZMv0we7H9j8Y8           0.00455    0.0792    -5.075       0.0570  \
0ZxZsjMMyLgjRV1XLWlIaS           0.00011    0.3960    -5.434       0.0872   
0Jc2SfIHv63JNsUZpunh54           0.74800    0.1060   -23.408       0.0394   

                          tempo  valence  
id                                        
4m3GHOgCNZMv0we7H9j8Y8  139.925   0.1610  
0ZxZsjMMyLgjRV1XLWlIaS  105.032   0.1280  
0Jc2SfIHv63JNsUZpunh54  124.266   0.0399

In [4]:
tracks_df = pd.read_csv("Data/tenyear_cleaned_for_kmeans.csv",index_col='id')
tracks_df

acousticness  danceability  duration_ms  energy   
id                                                                        
4m3GHOgCNZMv0we7H9j8Y8      0.022200         0.450       362880   0.849  \
0ZxZsjMMyLgjRV1XLWlIaS      0.000103         0.382       274133   0.943   
0Jc2SfIHv63JNsUZpunh54      0.852000         0.179       162120   0.167   
5QZunYrvUrJs3Mzrjl7fKV      0.080900         0.507       266547   0.770   
0X0zDB7RqpWOIwCHGr2Whu      0.002960         0.315       210640   0.925   
...                              ...           ...          ...     ...   
4KppkflX7I3vJQk7urOJaS      0.173000         0.875       163800   0.443   
1ehhGlTvjtHo2e4xJFB0SZ      0.016700         0.719       167468   0.385   
52eycxprLhK3lPcRLbQiVk      0.538000         0.514       180700   0.539   
3wYOGJYD31sLRmBgCvWxa4      0.071400         0.646       167308   0.761   
60RFlt48hm0l4Fu0JoccOl      0.109000         0.512       214787   0.428   

                        instrumentalness  liveness  loudness  speechiness   
id                                                                          
4m3GHOgCNZMv0we7H9j8Y8          0.004550    0.0792    -5.075       0.0570  \
0ZxZsjMMyLgjRV1XLWlIaS          0.000110    0.3960    -5.434       0.0872   
0Jc2SfIHv63JNsUZpunh54          0.748000    0.1060   -23.408       0.0394   
5QZunYrvUrJs3Mzrjl7fKV          0.000000    0.2140    -5.018       0.0424   
0X0zDB7RqpWOIwCHGr2Whu          0.064200    0.1140    -4.507       0.1170   
...                                  ...       ...       ...          ...   
4KppkflX7I3vJQk7urOJaS          0.000032    0.0891    -7.461       0.1430   
1ehhGlTvjtHo2e4xJFB0SZ          0.031300    0.1110   -10.907       0.0403   
52eycxprLhK3lPcRLbQiVk          0.002330    0.1080    -9.332       0.1050   
3wYOGJYD31sLRmBgCvWxa4          0.000000    0.2220    -2.557       0.0385   
60RFlt48hm0l4Fu0JoccOl          0.000000    0.1050    -7.387       0.0271   

                          tempo  valence  
id                                        
4m3GHOgCNZMv0we7H9j8Y8  139.925   0.1610  
0ZxZsjMMyLgjRV1XLWlIaS  105.032   0.1280  
0Jc2SfIHv63JNsUZpunh54  124.266   0.0399  
5QZunYrvUrJs3Mzrjl7fKV  155.945   0.4820  
0X0zDB7RqpWOIwCHGr2Whu  185.305   0.4150  
...                         ...      ...  
4KppkflX7I3vJQk7urOJaS  100.012   0.3060  
1ehhGlTvjtHo2e4xJFB0SZ  128.000   0.2700  
52eycxprLhK3lPcRLbQiVk  123.700   0.1530  
3wYOGJYD31sLRmBgCvWxa4  129.916   0.4720  
60RFlt48hm0l4Fu0JoccOl   80.588   0.3660  

[21656 rows x 10 columns]

In [5]:
#getting column names and indicies from old df
column_names = cleaned_tracks_df.columns
index = cleaned_tracks_df.index

#scaling data
scaler = StandardScaler()
scaled_data = scaler.fit_transform(cleaned_tracks_df)

#new df for scaled data
tracks_df_scaled = pd.DataFrame(scaled_data, columns=column_names, index=index)
tracks_df_scaled.head()

acousticness  danceability  duration_ms    energy   
id                                                                          
4m3GHOgCNZMv0we7H9j8Y8     -0.811238     -0.909532     1.643723  1.002060  \
0ZxZsjMMyLgjRV1XLWlIaS     -0.888078     -1.308428     0.605259  1.434322   
0Jc2SfIHv63JNsUZpunh54      2.074284     -2.499249    -0.705451 -2.134141   
5QZunYrvUrJs3Mzrjl7fKV     -0.607117     -0.575163     0.516492  0.638776   
0X0zDB7RqpWOIwCHGr2Whu     -0.878143     -1.701457    -0.137699  1.351549   

                        instrumentalness  liveness  loudness  speechiness   
id                                                                          
4m3GHOgCNZMv0we7H9j8Y8         -0.292517 -0.715717  0.488498    -0.430316  \
0ZxZsjMMyLgjRV1XLWlIaS         -0.312908  1.364415  0.412034    -0.156268   
0Jc2SfIHv63JNsUZpunh54          3.121720 -0.539746 -3.416253    -0.590026   
5QZunYrvUrJs3Mzrjl7fKV         -0.313413  0.169390  0.500638    -0.562803   
0X0zDB7RqpWOIwCHGr2Whu         -0.018579 -0.487218  0.609476     0.114150   

                           tempo   valence  
id                                          
4m3GHOgCNZMv0we7H9j8Y8  0.623063 -1.259246  
0ZxZsjMMyLgjRV1XLWlIaS -0.514938 -1.396740  
0Jc2SfIHv63JNsUZpunh54  0.112360 -1.763809  
5QZunYrvUrJs3Mzrjl7fKV  1.145539  0.078200  
0X0zDB7RqpWOIwCHGr2Whu  2.103086 -0.200955

In [6]:
# Create an empty list to store the inertia values
k = list(range(1,12))
inertia = []

# Create a for loop to compute the inertia with each possible value of k
for i in k:
    k_model = KMeans(n_clusters=i, random_state=42, n_init="auto")
    k_model.fit(tracks_df_scaled)
    inertia.append(k_model.inertia_)

# Create a dictionary with the data to plot the Elbow curve
elbow_dict = {"k": k, "inertia": inertia}

# Create a DataFrame with the data to plot the Elbow curve
elbow_df = pd.DataFrame(elbow_dict)
elbow_df.head()

k        inertia
0  1  216560.000000
1  2  173936.919767
2  3  158474.448027
3  4  140240.185221
4  5  130338.206476

In [7]:
#finding best k
elbow = elbow_df.hvplot.line(
    x='k',
    y='inertia',
    xticks=k,
    title='Elbow Curve using Original Scaled Data')
elbow

:Curve   [k]   (inertia)

k = 2 or 4 i guess?

In [8]:
#making model, fit/predict
k_model = KMeans(n_clusters=4, random_state=1, n_init="auto")

predictions = k_model.fit_predict(tracks_df_scaled)
print(predictions)

[0 0 2 ... 0 0 0]


In [9]:
#adding predictions to a df copy
tracks_df_predictions = cleaned_tracks_df.copy()
tracks_df_predictions["ClusterGroup"] = predictions
tracks_df_predictions.head()

acousticness  danceability  duration_ms  energy   
id                                                                        
4m3GHOgCNZMv0we7H9j8Y8      0.022200         0.450       362880   0.849  \
0ZxZsjMMyLgjRV1XLWlIaS      0.000103         0.382       274133   0.943   
0Jc2SfIHv63JNsUZpunh54      0.852000         0.179       162120   0.167   
5QZunYrvUrJs3Mzrjl7fKV      0.080900         0.507       266547   0.770   
0X0zDB7RqpWOIwCHGr2Whu      0.002960         0.315       210640   0.925   

                        instrumentalness  liveness  loudness  speechiness   
id                                                                          
4m3GHOgCNZMv0we7H9j8Y8           0.00455    0.0792    -5.075       0.0570  \
0ZxZsjMMyLgjRV1XLWlIaS           0.00011    0.3960    -5.434       0.0872   
0Jc2SfIHv63JNsUZpunh54           0.74800    0.1060   -23.408       0.0394   
5QZunYrvUrJs3Mzrjl7fKV           0.00000    0.2140    -5.018       0.0424   
0X0zDB7RqpWOIwCHGr2Whu           0.06420    0.1140    -4.507       0.1170   

                          tempo  valence  ClusterGroup  
id                                                      
4m3GHOgCNZMv0we7H9j8Y8  139.925   0.1610             0  
0ZxZsjMMyLgjRV1XLWlIaS  105.032   0.1280             0  
0Jc2SfIHv63JNsUZpunh54  124.266   0.0399             2  
5QZunYrvUrJs3Mzrjl7fKV  155.945   0.4820             0  
0X0zDB7RqpWOIwCHGr2Whu  185.305   0.4150             0

In [10]:
#track clusters 
track_clusters = tracks_df_predictions.hvplot.scatter(
    x="danceability",
    y="energy",
    by="ClusterGroup",
    hover_cols = "id",
    title="KMeans Cluster Groups"
)

track_clusters

:NdOverlay   [ClusterGroup]
   :Scatter   [danceability]   (energy,id)

In [11]:
#need to grab values of these columns
danceability = tracks_df_predictions['danceability'].values
energy = tracks_df_predictions['energy'].values

print(f"dance type {type(danceability)} \n energy type {type(energy)}")

dance type <class 'numpy.ndarray'> 
 energy type <class 'numpy.ndarray'>


In [12]:
#cKDTree only takes np arrays
test_points = np.column_stack([danceability, energy])
ckdtree = scipy.spatial.cKDTree(test_points)

In [13]:
#returns row number of songs that songs that have the closest dance/energy to dance/energy of some new song, rn just dummy numbers
def closest_point_id(ckdtree, x, y):
    #returns index of closest point
    return ckdtree.query([x, y],k=5)[1]

new_dance = 0.7
new_energy = 0.2
song_recommendations = closest_point_id(ckdtree, new_dance, new_energy)
song_recommendations

array([14706, 15363, 10391,  4081, 15028])

In [14]:
#grabbing the ids of the row numbers
song_ids = cleaned_tracks_df.iloc[song_recommendations,:].index.to_list()
song_ids

['7MdZQXUBijQxcBkYz4G1Z5',
 '0zhzkkSXFj60Y5fzb2j9hU',
 '7v52k3ozNqjKGlFPWDiudw',
 '6ZGqVXaJmhbYAK2DF8mWRR',
 '3V0nnQhqvbE3JmiDdnzQFQ']

same code as above, except this time it isolates the cluster group of the user's song before finding the closest data points (similar songs)

In [34]:
#isolates the cluster group of a specific song (user's song)
track_id = "0Jc2SfIHv63JNsUZpunh54"
user_song = tracks_df_predictions.loc[track_id]
group_number = int(user_song['ClusterGroup'])

user_song_cluster_group = tracks_df_predictions[tracks_df_predictions['ClusterGroup'] == group_number]
user_song_cluster_group

acousticness  danceability  duration_ms  energy   
id                                                                        
0Jc2SfIHv63JNsUZpunh54         0.852         0.179       162120  0.1670  \
4ksxLnn1ymLGRKnwhba45Y         0.996         0.500       327080  0.0104   
08DBDmvEgY2ZTVMVH2A8lt         0.451         0.543       205480  0.5090   
6oMuxrR8Aq74QG872Pd37Z         0.690         0.298       391107  0.4470   
5S0pF13mOsTnYweFwFy4D0         0.846         0.339       308440  0.1840   
...                              ...           ...          ...     ...   
76WMWYa1iqRTHZotPuuEuc         0.921         0.442       214012  0.2670   
1GofdWoWnV6F7sozQfoE79         0.973         0.415       207373  0.2620   
54OjRoNNwpExHizhCKhddk         0.932         0.491       188733  0.3670   
6lMqDaZjoqe6J1p8TdHuBZ         0.973         0.415       207373  0.2620   
6t5MVzUCfeK1ASDMkKadxW         0.786         0.501       192120  0.3490   

                        instrumentalness  liveness  loudness  speechiness   
id                                                                          
0Jc2SfIHv63JNsUZpunh54          0.748000    0.1060   -23.408       0.0394  \
4ksxLnn1ymLGRKnwhba45Y          0.949000    0.0573   -26.764       0.0622   
08DBDmvEgY2ZTVMVH2A8lt          0.734000    0.1120   -14.745       0.0418   
6oMuxrR8Aq74QG872Pd37Z          0.000000    0.6870    -8.499       0.1350   
5S0pF13mOsTnYweFwFy4D0          0.000003    0.1090    -8.624       0.0289   
...                                  ...       ...       ...          ...   
76WMWYa1iqRTHZotPuuEuc          0.000017    0.1210    -9.640       0.0582   
1GofdWoWnV6F7sozQfoE79          0.000003    0.1060   -12.530       0.0333   
54OjRoNNwpExHizhCKhddk          0.000876    0.1110    -7.164       0.0308   
6lMqDaZjoqe6J1p8TdHuBZ          0.000003    0.1060   -12.530       0.0333   
6t5MVzUCfeK1ASDMkKadxW          0.000000    0.1070   -10.883       0.3910   

                          tempo  valence  ClusterGroup  
id                                                      
0Jc2SfIHv63JNsUZpunh54  124.266   0.0399             2  
4ksxLnn1ymLGRKnwhba45Y  114.760   0.1330             2  
08DBDmvEgY2ZTVMVH2A8lt   99.974   0.0694             2  
6oMuxrR8Aq74QG872Pd37Z   75.041   0.2050             2  
5S0pF13mOsTnYweFwFy4D0   76.053   0.0989             2  
...                         ...      ...           ...  
76WMWYa1iqRTHZotPuuEuc   78.171   0.3220             2  
1GofdWoWnV6F7sozQfoE79  105.861   0.3110             2  
54OjRoNNwpExHizhCKhddk  134.105   0.4550             2  
6lMqDaZjoqe6J1p8TdHuBZ  105.861   0.3110             2  
6t5MVzUCfeK1ASDMkKadxW   72.855   0.3220             2  

[2936 rows x 11 columns]

In [36]:
#getting danceability/energy values
danceability2 = user_song_cluster_group['danceability'].values
energy2 = user_song_cluster_group['energy'].values

test_points2 = np.column_stack([danceability2, energy2])
ckdtree = scipy.spatial.cKDTree(test_points2)

In [30]:
#returns row number of songs that songs that have the closest dance/energy to dance/energy of some new song, rn just dummy numbers
def closest_point_id(ckdtree, x, y):
    #returns index of closest point
    return ckdtree.query([x, y],k=5)[1]

new_dance = 0.7
new_energy = 0.2
song_recommendations = closest_point_id(ckdtree, new_dance, new_energy)
song_recommendations

array([2070, 2142, 1626,  599, 2110])

In [35]:
#grabbing the ids of the row numbers
song_ids = cleaned_tracks_df.iloc[song_recommendations,:].index.to_list()
song_ids

['00s8dO3RWrFkBqC9JIy6ag',
 '6VN85VvNB8w1QbJCXW8rTC',
 '4xuToNvDiZHnDQVujjK49s',
 '6VBQ4DF4fwPJNA96RbMQWT',
 '6pgXtdQGyZODLuXK7ZrTCk']